In [1]:
import os
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
import numpy as np


pd.set_option('display.max_columns', 40)
pd.set_option('display.max_rows', 40)

In [2]:
PATH = os.path.dirname(os.getcwd())
DATA_PATH = f"{PATH}\\Datas"
MODEL_PATH = f"{PATH}\\Model" 

In [3]:
path = f"{PATH}\\ScopusData2018-2023"
filenames = []
for year in range(2018,2024):
    folder = f"{path}\\{year}"
    temp = [f for f in os.listdir(folder) if os.path.isfile(os.path.join(folder, f))]
    filenames += temp
print(len(filenames))

20216


In [4]:
data = pd.DataFrame()
n = 0 
N = len(filenames)
for filename in filenames:
    file_path = f"{path}\\{filename[0:4]}\\{filename}"
    temp = pd.read_json(file_path).T
    data = pd.concat([data, temp], axis=0, ignore_index=True)
    n+=1
    print(f"\r{n}/{N}" , end = "")
data.index = filenames


20216/20216

In [5]:
data.shape

(20216, 8)

In [6]:

def isColDict(col):
    for data in col:
        if (type(data) != dict):
            return False
    return True
def expandDict(df:pd.DataFrame):
    columns = df.columns
    toRemove = []
    for col in columns:
        if (isColDict(df[col])):
            print(df[col], df.shape , "\r", end="")
            expanded = pd.DataFrame(df[col].tolist(),index= df.index)
            toRemove.append(col)
            df = pd.concat([df, expanded] , axis = 1 )
            print(col, df.shape ,"finished\n-------------")
    df.drop(labels=toRemove, axis = 1,inplace=True)
    if(len(toRemove) == 0):
        return df
    else:
        return expandDict(df)
data2 = expandDict(data)

201800000    {'ait:process-info': {'ait:status': {'@state':...
201800001    {'ait:process-info': {'ait:status': {'@state':...
201800002    {'ait:process-info': {'ait:status': {'@state':...
201800003    {'ait:process-info': {'ait:status': {'@state':...
201800004    {'ait:process-info': {'ait:status': {'@state':...
                                   ...                        
202302885    {'ait:process-info': {'ait:status': {'@state':...
202302886    {'ait:process-info': {'ait:status': {'@state':...
202302887    {'ait:process-info': {'ait:status': {'@state':...
202302888    {'ait:process-info': {'ait:status': {'@state':...
202302889    {'ait:process-info': {'ait:status': {'@state':...
item (20216, 11) finished, dtype: object (20216, 8) 
-------------
201800000    {'srctype': 'b', 'eid': '2-s2.0-85077976956', ...
201800001    {'srctype': 'p', 'eid': '2-s2.0-85060936020', ...
201800002    {'srctype': 'j', 'eid': '2-s2.0-85052201238', ...
201800003    {'srctype': 'j', 'eid': '2-s2.0-850514

In [7]:
df = data2.loc[:, ~data2.columns.duplicated(keep='first')]

# 2. Define patterns to remove
drop_patterns = [
    '@',          # all XML attribute fields like @year, @type, etc.
    'ce:', "url", "link",      # internal Scopus tags
    'codencode', 'pii', 'itemid', '$',"eid", "issn",
    'tradenamegroup', 'chemicalgroup', 'manufacturergroup',
    'sequencebanks', 'descriptorgroup', "source-id","doi", "identifier",
    'volisspag', 'part', 'volumetitle',"tail","date-text","classifications",
    'preferred-sourcetitle', 'additional-srcinfo', 'issuetitle',
    'translated-sourcetitle', "prism:aggregationType", "subtypeDescription" ,"subtype",	"classifications",
    'dbcollection', 'external-source',
    'citation-language', 'abstract-language',
    'publishercopyright', 'article-number', 'prism:pageRange',
    'prism:startingPage', 'prism:endingPage',
    'xocs:meta', 'related-item', 'sourcetitle-abbrev', 'website',
    'author-group', 'contributor-group', 'grantlist', 'citation-title',"correspondence"
]

# 3. Drop any columns that match these patterns
to_drop = [c for c in df.columns if any(p in c for p in drop_patterns)]
df = df.drop(columns=to_drop, errors='ignore')
print(df.shape)
df.iloc[:4,:]

(20216, 27)


affiliation  \
201800000  [{'affiliation-city': 'Stanford', '@id': '6003...   
201800001  {'affiliation-city': 'Bangkok', '@id': '600281...   
201800002  {'affiliation-city': 'Bangkok', '@id': '600281...   
201800003  [{'affiliation-city': 'Hirosaki', '@id': '6003...   

                                                    idxterms  \
201800000                                               None   
201800001  {'mainterm': [{'$': 'Antenna dimensions', '@we...   
201800002  {'mainterm': [{'$': 'Circulating fluidized bed...   
201800003  {'mainterm': [{'$': 'Core-shell morphologies',...   

                       language  \
201800000  {'@xml:lang': 'eng'}   
201800001  {'@xml:lang': 'eng'}   
201800002  {'@xml:lang': 'eng'}   
201800003  {'@xml:lang': 'eng'}   

                                                authkeywords srctype  \
201800000                                               None       b   
201800001                                               None       p   
201800002  {'author-keyword': [{'@_fa': 'true', '$': 'Cir...       j   
201800003  {'author-keyword': [{'@_fa': 'true', '$': 'Enc...       j   

          prism:coverDate                                        prism:isbn  \
201800000      2018-12-31  [{'$': '9783319984858'}, {'$': '9783319984841'}]   
201800001      2018-12-31                                     9784885523151   
201800002      2018-12-31                                               NaN   
201800003      2018-12-31                                               NaN   

                                       prism:publicationName citedby-count  \
201800000  Radiology in Global Health: Strategies, Implem...             1   
201800001    Progress in Electromagnetics Research Symposium             1   
201800002                       Chemical Engineering Science            21   
201800003                            Applied Surface Science            37   

                                                    dc:title openaccess  \
201800000  Public health and international epidemiology f...          0   
201800001  Flexible Printed Active Antenna for Digital Te...          0   
201800002  Parametric study of hydrogen production via so...          0   
201800003  Superhydrophobic coating from fluoroalkylsilan...          0   

          openaccessFlag                                       dc:publisher  \
201800000          false                  Springer International Publishing   
201800001          false  Institute of Electrical and Electronics Engine...   
201800002          false                                       Elsevier Ltd   
201800003          false                                      Elsevier B.V.   

                                              dc:description prism:volume  \
201800000                                                NaN          NaN   
201800001  This paper presents the development of a flexi...  2018-August   
201800002  Computational fluid dynamics was applied for s...          192   
201800003  A superhydrophobic/superoleophilic mesh was su...          462   

          pubmed-id prism:issueIdentifier  \
201800000       NaN                   NaN   
201800001       NaN                   NaN   
201800002       NaN                   NaN   
201800003       NaN                   NaN   

                                                subject-area  \
201800000  [{'@_fa': 'true', '$': 'Medicine (all)', '@cod...   
201800001  [{'@_fa': 'true', '$': 'Electrical and Electro...   
201800002  [{'@_fa': 'true', '$': 'Chemistry (all)', '@co...   
201800003  [{'@_fa': 'true', '$': 'Chemistry (all)', '@co...   

                                                      author  \
201800000  [{'ce:given-name': 'Krit', 'preferred-name': {...   
201800001  [{'ce:given-name': 'Teerapong', 'preferred-nam...   
201800002  [{'ce:given-name': 'Kiattikhoon', 'preferred-n...   
201800003  [{'ce:given-name': 'Jittraporn', 'preferred-na...   

                                                   abstra

EDA

In [8]:
%pip install missingno

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [9]:
import missingno as msno
import matplotlib.pyplot as plt

In [10]:
print("Shape:", df.shape)
print("\nColumn names:\n", df.columns.tolist())

df.info()

Shape: (20216, 27)

Column names:
 ['affiliation', 'idxterms', 'language', 'authkeywords', 'srctype', 'prism:coverDate', 'prism:isbn', 'prism:publicationName', 'citedby-count', 'dc:title', 'openaccess', 'openaccessFlag', 'dc:publisher', 'dc:description', 'prism:volume', 'pubmed-id', 'prism:issueIdentifier', 'subject-area', 'author', 'abstracts', 'author-keywords', 'isbn', 'publisher', 'sourcetitle', 'month', 'year', 'day']
<class 'pandas.core.frame.DataFrame'>
Index: 20216 entries, 201800000 to 202302889
Data columns (total 27 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   affiliation            20216 non-null  object
 1   idxterms               11572 non-null  object
 2   language               20096 non-null  object
 3   authkeywords           16454 non-null  object
 4   srctype                20216 non-null  object
 5   prism:coverDate        20216 non-null  object
 6   prism:isbn             1649 non-null   objec

In [11]:
firstVisualization = df.copy()
firstVisualization

affiliation  \
201800000  [{'affiliation-city': 'Stanford', '@id': '6003...   
201800001  {'affiliation-city': 'Bangkok', '@id': '600281...   
201800002  {'affiliation-city': 'Bangkok', '@id': '600281...   
201800003  [{'affiliation-city': 'Hirosaki', '@id': '6003...   
201800004  [{'affiliation-city': 'Bangkok', '@id': '60028...   
...                                                      ...   
202302885  [{'affiliation-city': 'Bangkok', '@id': '60028...   
202302886  {'affiliation-city': 'Bangkok', '@id': '600281...   
202302887  [{'affiliation-city': 'Bangkok', '@id': '60028...   
202302888  [{'affiliation-city': 'Bangkok', '@id': '60028...   
202302889  [{'affiliation-city': 'Bangkok', '@id': '60028...   

                                                    idxterms  \
201800000                                               None   
201800001  {'mainterm': [{'$': 'Antenna dimensions', '@we...   
201800002  {'mainterm': [{'$': 'Circulating fluidized bed...   
201800003  {'mainterm': [{'$': 'Core-shell morphologies',...   
201800004  {'mainterm': [{'$': 'acpcPNA', '@weight': 'b',...   
...                                                      ...   
202302885  {'mainterm': [{'$': 'High selectivity', '@weig...   
202302886  {'mainterm': [{'$': 'Analytical tool', '@weigh...   
202302887                                               None   
202302888                                               None   
202302889                                               None   

                       language  \
201800000  {'@xml:lang': 'eng'}   
201800001  {'@xml:lang': 'eng'}   
201800002  {'@xml:lang': 'eng'}   
201800003  {'@xml:lang': 'eng'}   
201800004  {'@xml:lang': 'eng'}   
...                         ...   
202302885  {'@xml:lang': 'eng'}   
202302886  {'@xml:lang': 'eng'}   
202302887  {'@xml:lang': 'eng'}   
202302888  {'@xml:lang': 'eng'}   
202302889  {'@xml:lang': 'eng'}   

                                                authkeywords srctype  \
201800000                                               None       b   
201800001                                               None       p   
201800002  {'author-keyword': [{'@_fa': 'true', '$': 'Cir...       j   
201800003  {'author-keyword': [{'@_fa': 'true', '$': 'Enc...       j   
201800004  {'author-keyword': [{'@_fa': 'true', '$': 'acp...       j   
...                                                      ...     ...   
202302885  {'author-keyword': [{'@_fa': 'true', '$': 'Lon...       j   
202302886  {'author-keyword': [{'@_fa': 'true', '$': 'Bio...       j   
202302887  {'author-keyword': [{'@_fa': 'true', '$': 'con...       j   
202302888  {'author-keyword': [{'@_fa': 'true', '$': 'Ana...       j   
202302889  {'author-keyword': [{'@_fa': 'true', '$': 'Cam...       j   

          prism:coverDate                                        prism:isbn  \
201800000      2018-12-31  [{'$': '9783319984858'}, {'$': '9783319984841'}]   
201800001      2018-12-31                                     9784885523151   
201800002      2018-12-31                                               NaN   
201800003      2018-12-31                                               NaN   
201800004      2018-12-31                                               NaN   
...                   ...                                               ...   
202302885      2023-01-01                                               NaN   
202302886      2023-01-01                                               NaN   
202302887      2023-01-01                                               NaN   
202302888      2023-01-01                                               NaN   
202302889      2023-01-01                                               NaN   

                                       prism:publicationName citedby-count  \
201800000  Radiology in Global Health: Strategies, Implem...             1   
201800001    Progress in Electromagnetics Research Symposium             1   
201800002                       Chemical E

In [12]:
msno.bar(firstVisualization)
plt.title("Present Values per Column")
plt.show()


In [13]:
secondVisualization = firstVisualization.dropna(axis=1 ,thresh= 0.75*firstVisualization.shape[0])



In [14]:

def flattenAffiliation(df:pd.DataFrame):
    col = df["affiliation"]
    newData = []
    for row in col:
        city = []
        name = []
        country = []
        if (isinstance(row , list)):
            for item in row:
               city.append(item["affiliation-city"])
               name.append(item["affilname"]) 
               country.append(item["affiliation-country"])
        elif (isinstance(row , dict)):
            city.append(item["affiliation-city"])
            name.append(item["affilname"]) 
            country.append(item["affiliation-country"])
        newRow = [city , name , country]
        newData.append(newRow)
    return pd.DataFrame(newData, columns=["city" , "name" , "country"],index=df.index)
def flattenAuthor(l:list):
    authors = []
    for a in l:
        authors.append(a["preferred-name"]["ce:indexed-name"])
    return authors

In [15]:
affil = flattenAffiliation(secondVisualization)
secondVisualization = (pd.concat([affil,secondVisualization] , axis=1)).drop(labels="affiliation",axis = 1)


In [16]:
def flattenSubjectArea(l):
    if not isinstance(l,list):
        return ""
    result = ""
    for d in l:
        result += (d["$"] + ", ")
    return result.strip(", ")
def flattenKeywords(l):
    if isinstance(l, str):
        return l
    if not isinstance(l,dict):
        return ""
    result = ""
    l = l["author-keyword"]
    for d in l:
        try:
            result += d["$"] + ", "
        except:
            result += ""
    return result.strip(", ")
def flattenArtKeyword(l):
    if not isinstance(l , dict):
        return ""
    if isinstance(l, str):
        return l
    keywords = l["author-keyword"]
    result = ""
    print(keywords)
    for i in keywords:
        try:
            result += i["$"] + ", "
        except:
            result += ""
    return result.strip(", ")
def flattenPublisherName(d):
    if not isinstance(d,dict):
        return ""
    if isinstance(d, str):
        return d
    return d["publishername"]
def flattenLanguage(d):
    if not isinstance(d,dict):
        return ""
    return d["@xml:lang"]
def get_feature(df:pd.DataFrame, cat_col):
    num_features = []
    text_features = []
    for col in df.columns:
        column = df[col]
        for data in column:
            if pd.isna(data):
                continue
            elif isinstance(data,int) or isinstance(data,float):
                num_features.append(col)
                break
            elif isinstance(data,str) and col not in cat_col:
                text_features.append(col)
                break
    return num_features,text_features

In [17]:
secondVisualization["subject-area"] = secondVisualization["subject-area"].apply(flattenSubjectArea)
secondVisualization["authkeywords"] = secondVisualization["authkeywords"].apply(flattenKeywords)
secondVisualization["author"] = secondVisualization["author"].apply(flattenAuthor)
secondVisualization["author-keywords"] = secondVisualization["author-keywords"].apply(flattenArtKeyword)
secondVisualization["publisher"] = secondVisualization["publisher"].apply(flattenPublisherName)
secondVisualization["language"] = secondVisualization["language"].apply(flattenLanguage)
secondVisualization

[{'$': 'Circulating fluidized bed', '@xml:lang': 'eng'}, {'$': 'Computational fluid dynamics', '@xml:lang': 'eng'}, {'$': 'Multiphase flow models', '@xml:lang': 'eng'}, {'$': 'Riser', '@xml:lang': 'eng'}, {'$': 'Sorption enhanced steam methane reforming', '@xml:lang': 'eng'}]
[{'$': 'Encapsulation', '@xml:lang': 'eng'}, {'$': 'Fluoroalkylsilane', '@xml:lang': 'eng'}, {'$': 'Natural rubber', '@xml:lang': 'eng'}, {'$': 'Oil/water separation superhydrophobic/superoleophilic mesh', '@xml:lang': 'eng'}]
[{'$': 'acpcPNA', '@xml:lang': 'eng'}, {'$': 'Electrochemical impedance spectroscopy', '@xml:lang': 'eng'}, {'$': 'Mycobacterium tuberculosis', '@xml:lang': 'eng'}, {'$': 'Paper-based electrochemical DNA biosensor', '@xml:lang': 'eng'}]
[{'$': 'Design of experiment', '@xml:lang': 'eng'}, {'$': 'Optimal fleet size', '@xml:lang': 'eng'}, {'$': 'Outsourcing', '@xml:lang': 'eng'}, {'$': 'Simulation modelling', '@xml:lang': 'eng'}, {'$': 'Transportation contract', '@xml:lang': 'eng'}, {'$': 'Tran

city  \
201800000  [Stanford, Bangkok, Bangkok, Stanford, Palo Al...   
201800001                                        [Baltimore]   
201800002                                        [Baltimore]   
201800003  [Hirosaki, Bangkok, Pathum Thani, Nagoya, Nakh...   
201800004     [Bangkok, Pathum Thani, Fort Collins, Bangkok]   
...                                                      ...   
202302885                                 [Bangkok, Bangkok]   
202302886                                          [Bangkok]   
202302887                                  [Bangkok, London]   
202302888                               [Bangkok, Khon Kaen]   
202302889                              [Bangkok, Phnom Penh]   

                                                        name  \
201800000  [Stanford University School of Medicine, Chula...   
201800001  [Johns Hopkins Bloomberg School of Public Health]   
201800002  [Johns Hopkins Bloomberg School of Public Health]   
201800003  [Hirosaki University, Chulalongkorn University...   
201800004  [Chulalongkorn University, Thailand National E...   
...                                                      ...   
202302885  [Chulalongkorn University, Center of Excellenc...   
202302886  [Center of Excellence on Petrochemical and Mat...   
202302887  [Chulalongkorn University, UCL Institute of Ed...   
202302888   [Chulalongkorn University, Khon Kaen University]   
202302889  [Chulalongkorn University, Cambodia University...   

                                                     country language  \
201800000  [United States, Thailand, Thailand, United Sta...      eng   
201800001                                    [United States]      eng   
201800002                                    [United States]      eng   
201800003  [Japan, Thailand, Thailand, Japan, Thailand, T...      eng   
201800004      [Thailand, Thailand, United States, Thailand]      eng   
...                                                      ...      ...   
202302885                               [Thailand, Thailand]      eng   
202302886                                         [Thailand]      eng   
202302887                         [Thailand, United Kingdom]      eng   
202302888                               [Thailand, Thailand]      eng   
202302889                               [Thailand, Cambodia]      eng   

                                                authkeywords srctype  \
201800000                                                          b   
201800001                                                          p   
201800002  Circulating fluidized bed, Computational fluid...       j   
201800003  Encapsulation, Fluoroalkylsilane, Natural rubb...       j   
201800004  acpcPNA, Electrochemical impedance spectroscop...       j   
...                                                      ...     ...   
202302885  Long-chain olefins, Mesoporous KIT-6, Oleic ac...       j   
202302886  Biological hazards, chemical hazards, food con...       j   
202302887  conflict, Education, peacebuilding, social jus...       j   
202302888  Anabas testudineus, Black soldier fly, fish me...       j   
202302889  Cambodia, consumption, expenditure, Impact, in...       j   

          prism:coverDate                              prism:publicationName  \
201800000      2018-12-31  Radiology in Global Health: Strategies, Implem...   
201800001      2018-12-31    Progress in Electromagnetics Research Symposium   
201800002      2018-12-31                       Chemical Engineering Science   
201800003      2018-12-31                            Applied Surface Science   
201800004      2018-12-31                             Analytica Chimica Acta   
...                   ...                                                ...   
202302885      2023-01-01                                    Catalysis Today   
202302886      2023-01-01           Critical Reviews in Analytical Chemistry   
202302887      2023-01-01                               

In [18]:
secondVisualization['date'] = pd.to_datetime(
    secondVisualization.assign(
        month=secondVisualization['month'].fillna(1),
        day=secondVisualization['day'].fillna(1)
    )[['year', 'month', 'day']],
    errors='coerce'
)

In [20]:
secondVisualization.to_csv(f'{DATA_PATH}\\cleanedData.csv', index=True) 